<a href="https://colab.research.google.com/github/AnasAito/Graph-neural-networks/blob/main/GAT_dgl.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [2]:
pip install dgl

     |████████████████████████████████| 4.4MB 6.5MB/s 


- **dgl.function.copy_src(src, out)** - This code example is an edge UDF that computes the output using the source node feature data. To use this, specify the name of the source feature data (src) and the output name (out).
- **dgl.function.sum(msg, out)** - This code example is a node UDF that sums the messages in the node’s mailbox. To use this, specify the message name (msg) and the output name (out)

In [30]:
import dgl
import dgl.function as fn
import torch as th
import torch.nn as nn
import torch.nn.functional as F
from dgl import DGLGraph

## msg passing function 
# msg preparation 
gcn_msg = fn.copy_src(src='h', out='m')
#msg aggregation 
gcn_reduce = fn.sum(msg='m', out='h')

class GCNLayer(nn.Module):
    def __init__(self, in_feats, out_feats):
        super(GCNLayer, self).__init__()
        self.linear = nn.Linear(in_feats, out_feats)

    def forward(self, g, feature):
        # Creating a local scope so that all the stored ndata and edata
        # (such as the `'h'` ndata below) are automatically popped out
        # when the scope exits.
        with g.local_scope():
          ## init h feature vector with feat from input of layer
            g.ndata['h'] = feature
            ## update feat vectors 
            g.update_all(gcn_msg, gcn_reduce)
            ## extract h feat vectors 
            h = g.ndata['h']
            ## projection using linear layer 
            return self.linear(h)

class Net(nn.Module):
    def __init__(self):
        super(Net, self).__init__()
        self.layer1 = GCNLayer(1433, 16)
        self.layer2 = GCNLayer(16, 7)

    def forward(self, g, features):
        x = F.relu(self.layer1(g, features))
        x = self.layer2(g, x)
        return x
net = Net()
print(net)



Net(
  (layer1): GCNLayer(
    (linear): Linear(in_features=1433, out_features=16, bias=True)
  )
  (layer2): GCNLayer(
    (linear): Linear(in_features=16, out_features=7, bias=True)
  )
)


In [32]:
from dgl.data import citation_graph as citegrh
import networkx as nx
def load_cora_data():
    data = citegrh.load_cora()
    features = th.FloatTensor(data.features)
    labels = th.LongTensor(data.labels)
    train_mask = th.BoolTensor(data.train_mask)
    test_mask = th.BoolTensor(data.test_mask)
    g = DGLGraph(data.graph)
    return g, features, labels, train_mask, test_mask 

def evaluate(model, g, features, labels, mask):
    model.eval()
    with th.no_grad():
        logits = model(g, features)
        logits = logits[mask]
        labels = labels[mask]
        _, indices = th.max(logits, dim=1)
        correct = th.sum(indices == labels)
        return correct.item() * 1.0 / len(labels)

import time
import numpy as np
g, features, labels, train_mask, test_mask = load_cora_data()
optimizer = th.optim.Adam(net.parameters(), lr=1e-2)
dur = []
for epoch in range(50):
    if epoch >=3:
        t0 = time.time()

    net.train()
    logits = net(g, features)
    logp = F.log_softmax(logits, 1)
    loss = F.nll_loss(logp[train_mask], labels[train_mask])

    optimizer.zero_grad()
    loss.backward()
    optimizer.step()

    if epoch >=3:
        dur.append(time.time() - t0)

    acc = evaluate(net, g, features, labels, test_mask)
    print("Epoch {:05d} | Loss {:.4f} | Test Acc {:.4f} | Time(s) {:.4f}".format(
            epoch, loss.item(), acc, np.mean(dur)))

Extracting file to /root/.dgl/cora_v2
Finished data loading and preprocessing.
  NumNodes: 2708
  NumEdges: 10556
  NumFeats: 1433
  NumClasses: 7
  NumTrainingSamples: 140
  NumValidationSamples: 500
  NumTestSamples: 1000
Done saving data into cached files.


/usr/local/lib/python3.7/dist-packages/dgl/data/utils.py:285: UserWarning: Property dataset.feat will be deprecated, please use g.ndata['feat'] instead.
  warnings.warn('Property {} will be deprecated, please use {} instead.'.format(old, new))
/usr/local/lib/python3.7/dist-packages/dgl/data/utils.py:285: UserWarning: Property dataset.label will be deprecated, please use g.ndata['label'] instead.
  warnings.warn('Property {} will be deprecated, please use {} instead.'.format(old, new))
/usr/local/lib/python3.7/dist-packages/dgl/data/utils.py:285: UserWarning: Property dataset.train_mask will be deprecated, please use g.ndata['train_mask'] instead.
  warnings.warn('Property {} will be deprecated, please use {} instead.'.format(old, new))
/usr/local/lib/python3.7/dist-packages/dgl/data/utils.py:285: UserWarning: Property dataset.test_mask will be deprecated, please use g.ndata['test_mask'] instead.
  warnings.warn('Property {} will be deprecated, please use {} instead.'.format(old, new))


Epoch 00000 | Loss 1.9618 | Test Acc 0.1350 | Time(s) nan
Epoch 00001 | Loss 1.8474 | Test Acc 0.2030 | Time(s) nan
Epoch 00002 | Loss 1.7309 | Test Acc 0.2710 | Time(s) nan
Epoch 00003 | Loss 1.6235 | Test Acc 0.4400 | Time(s) 0.0313
Epoch 00004 | Loss 1.5353 | Test Acc 0.5040 | Time(s) 0.0336
Epoch 00005 | Loss 1.4625 | Test Acc 0.5660 | Time(s) 0.0331
Epoch 00006 | Loss 1.3943 | Test Acc 0.6120 | Time(s) 0.0325
Epoch 00007 | Loss 1.3260 | Test Acc 0.6310 | Time(s) 0.0320
Epoch 00008 | Loss 1.2579 | Test Acc 0.6430 | Time(s) 0.0315
Epoch 00009 | Loss 1.1906 | Test Acc 0.6560 | Time(s) 0.0310
Epoch 00010 | Loss 1.1238 | Test Acc 0.6770 | Time(s) 0.0307
Epoch 00011 | Loss 1.0570 | Test Acc 0.6880 | Time(s) 0.0304
Epoch 00012 | Loss 0.9939 | Test Acc 0.6940 | Time(s) 0.0302
Epoch 00013 | Loss 0.9354 | Test Acc 0.7050 | Time(s) 0.0309
Epoch 00014 | Loss 0.8802 | Test Acc 0.7040 | Time(s) 0.0308
Epoch 00015 | Loss 0.8276 | Test Acc 0.7030 | Time(s) 0.0312
Epoch 00016 | Loss 0.7778 | Test 

In [35]:
# GAT network construction 
import torch
import torch.nn as nn
import torch.nn.functional as F

## graph attention layer 
class GATLayer(nn.Module):
    def __init__(self, g, in_dim, out_dim):
        super(GATLayer, self).__init__()
        self.g = g
        # equation (1)
        self.fc = nn.Linear(in_dim, out_dim, bias=False)
        # equation (2)
        self.attn_fc = nn.Linear(2 * out_dim, 1, bias=False)
        self.reset_parameters()

    def reset_parameters(self):
        """Reinitialize learnable parameters."""
        gain = nn.init.calculate_gain('relu')
        nn.init.xavier_normal_(self.fc.weight, gain=gain)
        nn.init.xavier_normal_(self.attn_fc.weight, gain=gain)

    def edge_attention(self, edges):#for each edge in edges
        # edge UDF for equation (2)
        z2 = torch.cat([edges.src['z'], edges.dst['z']], dim=1)
        a = self.attn_fc(z2)
        return {'e': F.leaky_relu(a)}

    def message_func(self, edges):#for each edge in edges
        # message UDF for equation (3) & (4)
        return {'z': edges.src['z'], 'e': edges.data['e']}

    def reduce_func(self, nodes):#for each node in nodes 
        # reduce UDF for equation (3) & (4)
        # equation (3) 
        ## aggreagation of attention coef from edges with neighbors 
        alpha = F.softmax(nodes.mailbox['e'], dim=1)
        # equation (4)
        h = torch.sum(alpha * nodes.mailbox['z'], dim=1)
        return {'h': h}

    def forward(self, h):
        # equation (1)
        z = self.fc(h)
        self.g.ndata['z'] = z
        # equation (2)
        self.g.apply_edges(self.edge_attention)
        # equation (3) & (4)
        self.g.update_all(self.message_func, self.reduce_func)
        return self.g.ndata.pop('h')

## multi head attention  layer 
class MultiHeadGATLayer(nn.Module):
    def __init__(self, g, in_dim, out_dim, num_heads, merge='cat'):
        super(MultiHeadGATLayer, self).__init__()
        self.heads = nn.ModuleList()
        for i in range(num_heads):
            self.heads.append(GATLayer(g, in_dim, out_dim))
        self.merge = merge

    def forward(self, h):
      ## each GAT layer output h for each node => to make multi head stack layer 
        head_outs = [attn_head(h) for attn_head in self.heads]
        if self.merge == 'cat':
            # concat on the output feature dimension (dim=1)
            return torch.cat(head_outs, dim=1)
        else:
            # merge using average
            return torch.mean(torch.stack(head_outs))

## final network 
class GAT(nn.Module):
    def __init__(self, g, in_dim, hidden_dim, out_dim, num_heads):
        super(GAT, self).__init__()
        self.layer1 = MultiHeadGATLayer(g, in_dim, hidden_dim, num_heads)
        # Be aware that the input dimension is hidden_dim*num_heads since
        # multiple head outputs are concatenated together. Also, only
        # one attention head in the output layer.
        self.layer2 = MultiHeadGATLayer(g, hidden_dim * num_heads, out_dim, 1)

    def forward(self, h):
        h = self.layer1(h)
        h = F.elu(h)
        h = self.layer2(h)
        return h


In [57]:
features.shape

torch.Size([2708, 1433])

In [94]:
import time
import numpy as np
def load_cora_data():
    data = citegrh.load_cora()
    features = torch.FloatTensor(data.features)
    labels = torch.LongTensor(data.labels)
    mask_train = torch.BoolTensor(data.train_mask)
    mask_test = torch.BoolTensor(data.test_mask)
    g = DGLGraph(data.graph)
    return g, features, labels, mask_train,mask_test
g, features, labels, mask_train,mask_test = load_cora_data()





# create the model, 2 heads, each head has hidden size 8
net = GAT(g,
          in_dim=features.size()[1],
          hidden_dim=8,
          out_dim=7,## number of classes 
          num_heads=2)

# create optimizer
optimizer = torch.optim.Adam(net.parameters(), lr=1e-3)

# main loop
dur = []
logs=[]
for epoch in range(30):
    if epoch >= 3:
        t0 = time.time()

    logits = net(features)
    logp = F.log_softmax(logits, 1)
    logs.append(logp)
    loss = F.nll_loss(logp[mask_train], labels[mask_train])
    
    optimizer.zero_grad()
    loss.backward()
    optimizer.step()
    
    if epoch >= 3:
        dur.append(time.time() - t0)

    print("Epoch {:05d} | Loss {:.4f} | Time(s) {:.4f}".format(
        epoch, loss.item(), np.mean(dur)))
    #print('------------')
    #print(network_accuracy(net,g,features)[0])

  NumNodes: 2708
  NumEdges: 10556
  NumFeats: 1433
  NumClasses: 7
  NumTrainingSamples: 140
  NumValidationSamples: 500
  NumTestSamples: 1000
Done loading data from cached files.


/usr/local/lib/python3.7/dist-packages/dgl/data/utils.py:285: UserWarning:

Property dataset.feat will be deprecated, please use g.ndata['feat'] instead.

/usr/local/lib/python3.7/dist-packages/dgl/data/utils.py:285: UserWarning:

Property dataset.label will be deprecated, please use g.ndata['label'] instead.

/usr/local/lib/python3.7/dist-packages/dgl/data/utils.py:285: UserWarning:

Property dataset.train_mask will be deprecated, please use g.ndata['train_mask'] instead.

/usr/local/lib/python3.7/dist-packages/dgl/data/utils.py:285: UserWarning:

Property dataset.test_mask will be deprecated, please use g.ndata['test_mask'] instead.

/usr/local/lib/python3.7/dist-packages/dgl/data/utils.py:285: UserWarning:

Property dataset.graph will be deprecated, please use dataset[0] instead.

/usr/local/lib/python3.7/dist-packages/dgl/base.py:45: DGLWarning:

Recommend creating graphs by `dgl.graph(data)` instead of `dgl.DGLGraph(data)`.

/usr/local/lib/python3.7/dist-packages/numpy/core/fromnu

Epoch 00000 | Loss 1.9458 | Time(s) nan
Epoch 00001 | Loss 1.9440 | Time(s) nan
Epoch 00002 | Loss 1.9422 | Time(s) nan
Epoch 00003 | Loss 1.9404 | Time(s) 0.1527
Epoch 00004 | Loss 1.9386 | Time(s) 0.1530
Epoch 00005 | Loss 1.9368 | Time(s) 0.1554
Epoch 00006 | Loss 1.9350 | Time(s) 0.1545
Epoch 00007 | Loss 1.9332 | Time(s) 0.1525
Epoch 00008 | Loss 1.9314 | Time(s) 0.1518
Epoch 00009 | Loss 1.9296 | Time(s) 0.1518
Epoch 00010 | Loss 1.9278 | Time(s) 0.1512
Epoch 00011 | Loss 1.9260 | Time(s) 0.1508
Epoch 00012 | Loss 1.9241 | Time(s) 0.1503
Epoch 00013 | Loss 1.9223 | Time(s) 0.1498
Epoch 00014 | Loss 1.9205 | Time(s) 0.1499
Epoch 00015 | Loss 1.9186 | Time(s) 0.1497
Epoch 00016 | Loss 1.9167 | Time(s) 0.1505
Epoch 00017 | Loss 1.9149 | Time(s) 0.1503
Epoch 00018 | Loss 1.9130 | Time(s) 0.1498
Epoch 00019 | Loss 1.9111 | Time(s) 0.1490
Epoch 00020 | Loss 1.9092 | Time(s) 0.1487
Epoch 00021 | Loss 1.9072 | Time(s) 0.1480
Epoch 00022 | Loss 1.9053 | Time(s) 0.1491
Epoch 00023 | Loss 1

In [81]:
import numpy as np
from sklearn.manifold import TSNE
X = logs[0].detach().numpy()
X_embedded = TSNE(n_components=2).fit_transform(X)
X_embedded.shape


In [82]:
import numpy as np
from sklearn.manifold import TSNE
X = logs[-1].detach().numpy()
X_embedded = TSNE(n_components=2).fit_transform(X)
X_embedded.shape

import plotly.express as px
fig = px.scatter(x=X_embedded[:,1], y=X_embedded[:,0])
fig.show()

In [83]:
labels

tensor([3, 4, 4,  ..., 3, 3, 3])

In [84]:
import plotly.graph_objects as go

fig = go.Figure(data=go.Scatter(
    x=X_embedded[:,1],
    y=X_embedded[:,0],
    mode='markers',
    marker=dict(
                color=labels.detach().numpy())
))

fig.show()

In [86]:
import plotly.express as px
df = px.data.gapminder()
px.scatter(df, x="gdpPercap", y="lifeExp", animation_frame="year", animation_group="country",
           size="pop", color="continent", hover_name="country",
           log_x=True, size_max=55, range_x=[100,100000], range_y=[25,90])

In [87]:
df

country continent  year  ...   gdpPercap  iso_alpha  iso_num
0     Afghanistan      Asia  1952  ...  779.445314        AFG        4
1     Afghanistan      Asia  1957  ...  820.853030        AFG        4
2     Afghanistan      Asia  1962  ...  853.100710        AFG        4
3     Afghanistan      Asia  1967  ...  836.197138        AFG        4
4     Afghanistan      Asia  1972  ...  739.981106        AFG        4
...           ...       ...   ...  ...         ...        ...      ...
1699     Zimbabwe    Africa  1987  ...  706.157306        ZWE      716
1700     Zimbabwe    Africa  1992  ...  693.420786        ZWE      716
1701     Zimbabwe    Africa  1997  ...  792.449960        ZWE      716
1702     Zimbabwe    Africa  2002  ...  672.038623        ZWE      716
1703     Zimbabwe    Africa  2007  ...  469.709298        ZWE      716

[1704 rows x 8 columns]

In [95]:
import numpy as np
from sklearn.manifold import TSNE


rows = []
labels = labels.detach().numpy()
for log_index,log in enumerate(logs) : 
  print(log_index)
  ## extract data 
  log = log.detach().numpy()
  log_embedded = TSNE(n_components=2).fit_transform(log)
  x_list = log_embedded[:,0]
  y_list=log_embedded[:,1]
  
  # create row 
  for i,x in enumerate(x_list):
          rows.append([x_list[i],y_list[i],labels[i],log_index] )


# import pandas as pd
import pandas as pd 
    

    
df = pd.DataFrame(rows, columns =['x', 'y', 'label','itter'], dtype = float)
df

0
1
2
3
4
5
6
7
8
9
10
11
12
13
14
15
16
17
18
19
20
21
22
23
24
25
26
27
28
29


x          y  label  itter
0     -45.714668  11.483968    3.0    0.0
1     -12.378349  47.615654    4.0    0.0
2      23.499897 -23.754753    4.0    0.0
3      62.082592  18.319235    0.0    0.0
4     -17.354248  55.037399    3.0    0.0
...          ...        ...    ...    ...
81235  -9.867057  37.580006    3.0   29.0
81236   7.572294  52.401196    3.0   29.0
81237  14.788150  -1.924704    3.0   29.0
81238 -22.727135  25.055161    3.0   29.0
81239  -6.419464  23.796007    3.0   29.0

[81240 rows x 4 columns]

In [99]:
import plotly.express as px
df = pd.DataFrame(rows, columns =['x', 'y', 'label','itter'], dtype = float)
df
px.scatter(df, x="x", y="y", animation_frame="itter", #animation_group="country",
        color="label", range_x=[-100,100], range_y=[-100,100] )